### Strategy
Since Mostly the portfolio fails if the withdrawls happens during Market Crash,
We can use the Debt to make sure the withdrawls are not happening during crash period.

Logic:
Transfer Money from Equity to Debt on Good Months

In [1]:
import pandas as pd 
import math
import plotly.express as px


In [2]:
sensex_1980 = "../data/SnP-Sensex-1980.csv"
sensex_df = pd.read_csv(sensex_1980, header=0)
sensex_df
del sensex_df["Low"]
del sensex_df["Open"]
del sensex_df["High"]
sensex_df["Returns"] = sensex_df["Close"].pct_change()
sensex_df= sensex_df.fillna(0)

In [3]:
sensex_df

Month     Close   Returns
0      January-1991    982.32  0.000000
1     February-1991   1220.41  0.242375
2        March-1991   1167.97 -0.042969
3        April-1991   1235.11  0.057484
4          May-1991   1307.34  0.058481
..              ...       ...       ...
353       June-2020  34915.80  0.076847
354       July-2020  37606.89  0.077074
355     August-2020  38628.29  0.027160
356  September-2020  38067.93 -0.014506
357    October-2020  40509.49  0.064137

[358 rows x 3 columns]

#### Effective Return = Return On Equity + Return on Debt - Inflated Value fo Withdrawl

In [37]:
DEBT_RETURN = 1.08
INFLATION_ANNUAL = 1.05
SWR = 4
SWR_RANGES = [1,2,3,4,5]
MONTHLY_DEBT_RETURN = math.pow(DEBT_RETURN, 1/12) - 1
MONTHLY_INFLATION = math.pow(INFLATION_ANNUAL, 1/12) - 1
FIRST_WITHDRAWAL = SWR/12
EQUITY_SHARE = .8
DEBT_SHARE = 1 - EQUITY_SHARE
INITIAL_NVESTMENT = 100
DATAPOINTS = len(sensex_df.index)
EXCLUDE_RESULT = 60 # Last 1 year , result will excluded for performance calculation

In [38]:
def calculate_withdrawls(initial_withdrawal):
    withdrawals = list()
    withdrawals_values = initial_withdrawal
    for i in range(DATAPOINTS):
        withdrawals_values = (1+MONTHLY_INFLATION)*withdrawals_values
        withdrawals.append(withdrawals_values)
    return withdrawals

In [39]:
def calculate_inflated_portfolio(initial_investment):
    inflated_portfolio = list()
    inflated_values = initial_investment
    inflated_portfolio.append(initial_investment)
    for i in range(DATAPOINTS):
        inflated_values = (1+MONTHLY_INFLATION)*inflated_values
        inflated_portfolio.append(inflated_values)
    return inflated_portfolio
INFLATED_PORTFOLIO = calculate_inflated_portfolio(INITIAL_NVESTMENT*EQUITY_SHARE)

In [40]:
def generate_portfolio(main_index, withdrawals):
    equity = INITIAL_NVESTMENT*EQUITY_SHARE
    debt = INITIAL_NVESTMENT*DEBT_SHARE
    current_month_amount = equity + debt
    monthly_portfolio_value = list()
    for index, row in sensex_df.iterrows():
        if main_index < index:
            if equity >= (INFLATED_PORTFOLIO[index] + 2*withdrawals[index]): ## On very Good Times add, Move some protion to Debt
                debt = (1+ MONTHLY_DEBT_RETURN)*debt + withdrawals[index]
                equity = (1 + row["Returns"])*equity - 2*withdrawals[index]
            elif equity >= (INFLATED_PORTFOLIO[index] + withdrawals[index]): ## Deduct From equity
                debt = (1+ MONTHLY_DEBT_RETURN)*debt 
                equity = (1 + row["Returns"])*equity - withdrawals[index]
            else:
                debt = (1+ MONTHLY_DEBT_RETURN)*debt - withdrawals[index]
                equity = (1 + row["Returns"])*equity
            total_value = equity + debt
            monthly_portfolio_value.append(total_value)
        elif main_index == index:
            monthly_portfolio_value.append(equity + debt)
        else:
            monthly_portfolio_value.append(None)
    return monthly_portfolio_value

In [41]:
performance_at_swr = dict()
for swr in SWR_RANGES:
    initial_withdrawal = swr/12
    withdrawals = calculate_withdrawls(initial_withdrawal)
    portfolio_growth_df = pd.DataFrame()
    for main_index, main_row in sensex_df.iterrows():
        monthly_portfolio_value  = generate_portfolio(main_index, withdrawals)
        portfolio_growth_df.insert(main_index, main_row["Month"], monthly_portfolio_value)
    performance_at_swr[swr] = portfolio_growth_df

In [42]:
def inflated_value(initial_value, timeperiod, monthly_inflation):
    return initial_value * (pow((1 + monthly_inflation ), timeperiod)) 

In [43]:
## Calculate the inflated value of portfolio
inflated_corpus = list()
total_months = len(sensex_df.index)-1
for month  in sensex_df["Month"]:
    corpus_value = inflated_value(100, total_months, MONTHLY_INFLATION)
    inflated_corpus.append((month, corpus_value))
    total_months -= 1
inflated_corpus_df = pd.DataFrame.from_records(inflated_corpus, columns=["Month", "corpus"])
inflated_corpus_df

Month      corpus
0      January-1991  426.954551
1     February-1991  425.222144
2        March-1991  423.496765
3        April-1991  421.778388
4          May-1991  420.066983
..              ...         ...
353       June-2020  101.639636
354       July-2020  101.227223
355     August-2020  100.816485
356  September-2020  100.407412
357    October-2020  100.000000

[358 rows x 2 columns]

In [44]:
## Current Value of Portfolio
def get_current_value(performace_df):
    current_value_df  = performace_df.tail(1)
    current_value_df = current_value_df.transpose()
    current_value_df.columns = ["corpus"]
    current_value_df['Month'] = current_value_df.index
    current_value_df = current_value_df[['Month', 'corpus']]
    current_value_df = current_value_df.reset_index(drop=True)
    return current_value_df
get_current_value(performance_at_swr[4])

Month       corpus
0      January-1991  1749.494099
1     February-1991  1324.785740
2        March-1991  1403.338257
3        April-1991  1314.677305
4          May-1991  1221.619190
..              ...          ...
353       June-2020   107.600018
354       July-2020   102.266120
355     August-2020   101.292875
356  September-2020   103.830655
357    October-2020   100.000000

[358 rows x 2 columns]

In [45]:
performance_list = list()
for swr in SWR_RANGES:
    current_value_df = get_current_value(performance_at_swr[swr])
    temp_current_value_df = current_value_df[:-EXCLUDE_RESULT]
    temp_inflated_corpus_df = inflated_corpus_df[:-EXCLUDE_RESULT]
    preservation_result =  temp_current_value_df['corpus'] - temp_inflated_corpus_df['corpus']
    preservation_result_df = pd.DataFrame(preservation_result)
    preservation_status = preservation_result_df.apply(lambda x: True if x['corpus'] >0 else False , axis=1)
    success = len(preservation_status[preservation_status == True].index)
    performance_list.append((swr, success/len(preservation_status)))

In [46]:
performance_df = pd.DataFrame.from_records(performance_list, columns=["SWR", "Performance"])

In [47]:
performance_df

SWR  Performance
0    1     0.912752
1    2     0.651007
2    3     0.607383
3    4     0.510067
4    5     0.285235

In [34]:
fig = px.line(performance_at_swr[4], title='SWR 4% - 1991 - 2020')
fig.show()

Years Failed

In [35]:
current_value_df = get_current_value(performance_at_swr[4])
temp_current_value_df = current_value_df[:-EXCLUDE_RESULT]
temp_inflated_corpus_df = inflated_corpus_df[:-EXCLUDE_RESULT]
preservation_result =  temp_current_value_df['corpus'] - temp_inflated_corpus_df['corpus']
preservation_result


0      637.824084
1      450.025384
2      483.870693
3      444.584968
4      403.737802
          ...    
293    -80.002879
294    -79.167099
295    -72.448627
296    -70.375361
297    -70.141328
Name: corpus, Length: 298, dtype: float64

In [36]:
preservation_result_df = pd.DataFrame(preservation_result)
preservation_result_df

corpus
0    637.824084
1    450.025384
2    483.870693
3    444.584968
4    403.737802
..          ...
293  -80.002879
294  -79.167099
295  -72.448627
296  -70.375361
297  -70.141328

[298 rows x 1 columns]